In [1]:
import numpy as np
import pandas as pd
import textwrap
import nltk
from nltk import word_tokenize
from nltk.tokenize.treebank import TreebankWordDetokenizer

In [3]:
nltk.download('punkt')

[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\ashut\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!


True

In [4]:
df=pd.read_csv("bbc_text_cls.csv")
df.head()

text    labels
0  Ad sales boost Time Warner profit\n\nQuarterly...  business
1  Dollar gains on Greenspan speech\n\nThe dollar...  business
2  Yukos unit buyer faces loan claim\n\nThe owner...  business
3  High fuel prices hit BA's profits\n\nBritish A...  business
4  Pernod takeover talk lifts Domecq\n\nShares in...  business

In [5]:
lables=set(df['labels'])
lables

{'business', 'entertainment', 'politics', 'sport', 'tech'}

In [6]:
# Pick a label whose data we want to train from
label = 'business'

In [7]:
texts = df[df['labels'] == label]['text']
texts.head()

0    Ad sales boost Time Warner profit\n\nQuarterly...
1    Dollar gains on Greenspan speech\n\nThe dollar...
2    Yukos unit buyer faces loan claim\n\nThe owner...
3    High fuel prices hit BA's profits\n\nBritish A...
4    Pernod takeover talk lifts Domecq\n\nShares in...
Name: text, dtype: object

In [23]:
# collect counts
probs = {} # key: (w(t-1), w(t+1)), value: {w(t): count(w(t))}

for doc in texts:
  lines = doc.split("\n")
  for line in lines:
    tokens = word_tokenize(line)
    # print(tokens)  
    for i in range(len(tokens) - 2): #len(token)-2 bcus we need to find till 2nd last word
      t_0 = tokens[i]
      t_1 = tokens[i + 1]
      t_2 = tokens[i + 2]
      key = (t_0, t_2)
      if key not in probs:
        probs[key] = {}
      
      # add count for middle token
      if t_1 not in probs[key]:
        probs[key][t_1] = 1
      else:
        probs[key][t_1] += 1
# print(probs)        

{('Ad', 'boost'): {'sales': 1}, ('sales', 'Time'): {'boost': 1}, ('boost', 'Warner'): {'Time': 1}, ('Time', 'profit'): {'Warner': 1}, ('Quarterly', 'at'): {'profits': 1}, ('profits', 'US'): {'at': 1}, ('at', 'media'): {'US': 1}, ('US', 'giant'): {'media': 1, 'telecoms': 1, 'banking': 2, 'foods': 1, 'retail': 1, 'oil': 2, 'mortgage': 1, 'agrochemical': 1}, ('media', 'TimeWarner'): {'giant': 1}, ('giant', 'jumped'): {'TimeWarner': 1}, ('TimeWarner', '76'): {'jumped': 1}, ('jumped', '%'): {'76': 1, '1.8': 1, '11': 1, '6': 1, '10.7': 1, '7': 1, '22': 1}, ('76', 'to'): {'%': 1}, ('%', '$'): {'to': 17, 'at': 5}, ('to', '1.13bn'): {'$': 1}, ('$', '('): {'1.13bn': 1, '900m': 1, '280bn': 3, '86m': 1, '20bn': 2, '671.7bn': 1, '27.5bn': 4, '32bn': 1, '4bn': 1, '2bn': 3, '11bn': 5, '850m': 1, '300bn': 1, '186m': 1, '3.25bn': 1, '6bn': 3, '546m': 1, '16.6bn': 1, '11.5bn': 1, '3bn': 1, '102.6bn': 1, '427bn': 2, '676m': 1, '375m': 1, '1,000bn': 1, '515m': 1, '28.3bn': 1, '458.4m': 1, '35bn': 1, '800m

In [9]:
# normalize probabilities
for key, d in probs.items():
  # d should represent a distribution
  total = sum(d.values())
  for k, v in d.items():
    d[k] = v / total

In [10]:
probs

{('Ad', 'boost'): {'sales': 1.0},
 ('sales', 'Time'): {'boost': 1.0},
 ('boost', 'Warner'): {'Time': 1.0},
 ('Time', 'profit'): {'Warner': 1.0},
 ('Quarterly', 'at'): {'profits': 1.0},
 ('profits', 'US'): {'at': 1.0},
 ('at', 'media'): {'US': 1.0},
 ('US', 'giant'): {'media': 0.1,
  'telecoms': 0.1,
  'banking': 0.2,
  'foods': 0.1,
  'retail': 0.1,
  'oil': 0.2,
  'mortgage': 0.1,
  'agrochemical': 0.1},
 ('media', 'TimeWarner'): {'giant': 1.0},
 ('giant', 'jumped'): {'TimeWarner': 1.0},
 ('TimeWarner', '76'): {'jumped': 1.0},
 ('jumped', '%'): {'76': 0.14285714285714285,
  '1.8': 0.14285714285714285,
  '11': 0.14285714285714285,
  '6': 0.14285714285714285,
  '10.7': 0.14285714285714285,
  '7': 0.14285714285714285,
  '22': 0.14285714285714285},
 ('76', 'to'): {'%': 1.0},
 ('%', '$'): {'to': 0.7727272727272727, 'at': 0.22727272727272727},
 ('to', '1.13bn'): {'$': 1.0},
 ('$', '('): {'1.13bn': 0.006802721088435374,
  '900m': 0.006802721088435374,
  '280bn': 0.02040816326530612,
  '86m':

In [11]:
def spin_document(doc):
  # split the document into lines (paragraphs)
  lines = doc.split("\n")
  output = []
  for line in lines:
    if line:
      new_line = spin_line(line)
    else:
      new_line = line
    output.append(new_line)
  return "\n".join(output)

In [14]:
detokenizer = TreebankWordDetokenizer()


In [15]:
texts.iloc[0].split("\n")[2]

'Quarterly profits at US media giant TimeWarner jumped 76% to $1.13bn (£600m) for the three months to December, from $639m year-earlier.'

In [16]:
detokenizer.detokenize(word_tokenize(texts.iloc[0].split("\n")[2]))

'Quarterly profits at US media giant TimeWarner jumped 76% to $1.13bn (£600m) for the three months to December, from $639m year-earlier.'

In [17]:
def sample_word(d):
  p0 = np.random.random()
  cumulative = 0
  for t, p in d.items():
    cumulative += p
    if p0 < cumulative:
      return t
  assert(False) # should never get here

In [18]:
def spin_line(line):
  tokens = word_tokenize(line)
  i = 0
  output = [tokens[0]]
  while i < (len(tokens) - 2):
    t_0 = tokens[i]
    t_1 = tokens[i + 1]
    t_2 = tokens[i + 2]
    key = (t_0, t_2)
    p_dist = probs[key]
    if len(p_dist) > 1 and np.random.random() < 0.3:
      # let's replace the middle word
      middle = sample_word(p_dist)
      output.append(t_1)
      output.append("<" + middle + ">")
      output.append(t_2)

      # we won't replace the 3rd token since the middle
      # token was dependent on it
      # instead, skip ahead 2 steps
      i += 2
    else:
      # we won't replace this middle word
      output.append(t_1)
      i += 1
  # append the final token - only if there was no replacement
  if i == len(tokens) - 2:
    output.append(tokens[-1])
  return detokenizer.detokenize(output)

In [19]:
np.random.seed(1234)

In [20]:
i = np.random.choice(texts.shape[0])
doc = texts.iloc[i]
new_doc = spin_document(doc)

In [24]:
print(textwrap.fill(
    new_doc, replace_whitespace=False, fix_sentence_endings=True))

Bombardier chief to leave company

Shares in train and plane-making
giant Bombardier have fallen to <to> a 10-year low following <against>
the departure <hands> of its chief executive and two members of the
<key> board.

Paul Tellier, who <which> was also Bombardier's
president <epicentre>, left the company amid an ongoing <£80m>
restructuring . Laurent Beaudoin, part of the family that controls the
Montreal-based firm, will take on <over> the role of CEO under a newly
created management structure . Analysts said <believe> the
resignations seem to have stemmed from a boardroom dispute . Under Mr
Tellier's tenure at the company <subsidy>, which began in January
<July> 2003, plans <according> to cut the worldwide workforce of
75,000 by almost <signing> a third <movement> by 2006 were announced .
The firm's snowmobile <auto> division and defence services unit were
also sold and Bombardier started the development <future> of a new
aircraft seating 110 to 135 passengers.

Mr Tellier had ind